In [3]:
import torch
import numpy as np
from scipy.io import mmread
import torch.nn.functional as F
from torch_geometric.data import Data
from torch_geometric.nn import SAGEConv
from sklearn.metrics.pairwise import euclidean_distances
import torch.optim as optim
from sklearn.cluster import KMeans
import torch_geometric.utils as pyg_utils

In [4]:
#check cuda 
print(torch.cuda.is_available()) 
print(torch.version.cuda)
print(torch.__version__)

True
12.4
2.4.1


In [5]:
rawData = mmread('scRNA.mtx')
coo_matrix = rawData.tocoo()
print(coo_matrix)
print(coo_matrix.shape)

<COOrdinate sparse matrix of dtype 'float64'
	with 86422438 stored elements and shape (34619, 27180)>
  Coords	Values
  (30, 0)	878.85046
  (44, 0)	2636.5513
  (58, 0)	878.85046
  (74, 0)	878.85046
  (77, 0)	878.85046
  (109, 0)	878.85046
  (225, 0)	3515.4019
  (247, 0)	878.85046
  (272, 0)	878.85046
  (273, 0)	1318.2756
  (365, 0)	878.85046
  (366, 0)	2636.5513
  (421, 0)	878.85046
  (431, 0)	1757.7009
  (440, 0)	878.85046
  (442, 0)	5273.1025
  (499, 0)	16698.158
  (594, 0)	878.85046
  (649, 0)	1757.7009
  (688, 0)	878.85046
  (706, 0)	878.85046
  (831, 0)	1757.7009
  (835, 0)	2636.5513
  (867, 0)	878.85046
  (911, 0)	2636.5513
  :	:
  (32162, 27179)	142.14685
  (32202, 27179)	88.841736
  (32298, 27179)	177.68347
  (32423, 27179)	59.227825
  (32425, 27179)	177.68347
  (32564, 27179)	88.841736
  (33015, 27179)	177.68347
  (33454, 27179)	177.68347
  (33504, 27179)	177.68347
  (33538, 27179)	177.68347
  (33578, 27179)	88.841736
  (33636, 27179)	177.68347
  (33647, 27179)	284.01257
  (33

In [16]:
def clean_and_split_data(coo_matrix, max_number):
    #get only non-zero values
    total_nnz = coo_matrix.nnz 

    # Ensure max_nnz doesn’t exceed total
    if max_number >= total_nnz:
        raise ValueError(f"max_nnz ({max_number}) must be less than total non-zero elements ({total_nnz})")
    
    rows = coo_matrix.row
    cols = coo_matrix.col
    data = coo_matrix.data
    
    selected_indices = np.arange(max_number)  

    selected = coo_matrix.__class__(
        (data[selected_indices], (rows[selected_indices], cols[selected_indices])),
        shape=coo_matrix.shape
    )
    
    return selected

processed_data = clean_and_split_data(coo_matrix=coo_matrix, max_number=50000)
print(processed_data)

<COOrdinate sparse matrix of dtype 'float64'
	with 50000 stored elements and shape (34619, 27180)>
  Coords	Values
  (30, 0)	878.85046
  (44, 0)	2636.5513
  (58, 0)	878.85046
  (74, 0)	878.85046
  (77, 0)	878.85046
  (109, 0)	878.85046
  (225, 0)	3515.4019
  (247, 0)	878.85046
  (272, 0)	878.85046
  (273, 0)	1318.2756
  (365, 0)	878.85046
  (366, 0)	2636.5513
  (421, 0)	878.85046
  (431, 0)	1757.7009
  (440, 0)	878.85046
  (442, 0)	5273.1025
  (499, 0)	16698.158
  (594, 0)	878.85046
  (649, 0)	1757.7009
  (688, 0)	878.85046
  (706, 0)	878.85046
  (831, 0)	1757.7009
  (835, 0)	2636.5513
  (867, 0)	878.85046
  (911, 0)	2636.5513
  :	:
  (12449, 15)	35.81332
  (12455, 15)	214.87991
  (12457, 15)	35.81332
  (12463, 15)	35.81332
  (12472, 15)	35.81332
  (12478, 15)	214.87991
  (12482, 15)	35.81332
  (12490, 15)	35.81332
  (12500, 15)	71.62664
  (12503, 15)	107.43996
  (12505, 15)	143.25328
  (12508, 15)	429.75983
  (12511, 15)	179.0666
  (12514, 15)	35.81332
  (12520, 15)	250.69324
  (12525

In [ ]:
def build_cell_to_cell_graph_normal(data, threshold):   

    gene_expression = data.data
    outliers = []
    x = torch.tensor(gene_expression, dtype=torch.float32).unsqueeze(1)

    k = 2  
    distances = euclidean_distances(x, x)

    edge_index_list = []

    for i in range(len(gene_expression)):
        nearest_neighbors = np.argsort(distances[i])[1:k+1]  
        for j in nearest_neighbors:
            if distances[i, j] <= threshold:
                edge_index_list.append((i, j))
            else:
                outliers.append(int(j))

    edge_index_np = np.array(edge_index_list).T
    edge_index = torch.tensor(edge_index_np, dtype=torch.long) if edge_index_np.size > 0 else torch.empty((2, 0), dtype=torch.long)

    source_cells = edge_index_np[0]
    target_cells = edge_index_np[1]

    # for src, tgt in zip(source_cells, target_cells):
    #     print(f"Cell {src} is connected to Cell {tgt}")

  
    cleaned_outliers = list(set(outliers))
    print(cleaned_outliers)
    
  
    data = Data(edge_index=edge_index, x=x)
    return data

py_data = build_cell_to_cell_graph_normal(processed_data, threshold=500)

c:\Users\shera\anaconda3\envs\scRareCellDetect\Lib\site-packages\sklearn\metrics\pairwise.py:611: RuntimeWarning: overflow encountered in scalar multiply
  + (x_density * n_samples_X * y_density * n_samples_Y)


Cell 0 is connected to Cell 360
Cell 0 is connected to Cell 359
Cell 1 is connected to Cell 22
Cell 1 is connected to Cell 508
Cell 2 is connected to Cell 360
Cell 2 is connected to Cell 359
Cell 3 is connected to Cell 360
Cell 3 is connected to Cell 359
Cell 4 is connected to Cell 360
Cell 4 is connected to Cell 359
Cell 5 is connected to Cell 360
Cell 5 is connected to Cell 359
Cell 6 is connected to Cell 510
Cell 6 is connected to Cell 506
Cell 7 is connected to Cell 360
Cell 7 is connected to Cell 359
Cell 8 is connected to Cell 360
Cell 8 is connected to Cell 359
Cell 9 is connected to Cell 562
Cell 9 is connected to Cell 39547
Cell 10 is connected to Cell 360
Cell 10 is connected to Cell 359
Cell 11 is connected to Cell 22
Cell 11 is connected to Cell 508
Cell 12 is connected to Cell 360
Cell 12 is connected to Cell 359
Cell 13 is connected to Cell 498
Cell 13 is connected to Cell 169
Cell 14 is connected to Cell 360
Cell 14 is connected to Cell 359
Cell 15 is connected to Cell 2

In [18]:
class GraphSAGE(torch.nn.Module):
    def __init__(self, in_channels, hidden_channels, out_channels, num_layers=2):
        super(GraphSAGE, self).__init__()
        self.convs = torch.nn.ModuleList()
        self.convs.append(SAGEConv(in_channels, hidden_channels))  
        
        for _ in range(num_layers - 2):  
            self.convs.append(SAGEConv(hidden_channels, hidden_channels))
        
        self.convs.append(SAGEConv(hidden_channels, out_channels))  

    def forward(self, x, edge_index):
        for conv in self.convs[:-1]: 
            x = conv(x, edge_index)
            x = F.relu(x)
            x = F.dropout(x, p=0.5, training=self.training)
        x = self.convs[-1](x, edge_index) 
        return x  